<a href="https://colab.research.google.com/github/VENKATESH-GUNABALAN/Asteroid_Data_viewer/blob/main/PROJECT_1_NASA.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>



# > IMPORTING REQUESTS & **EXTENSIONS**



In [ ]:
import requests
import json
from datetime import datetime
!pip install mysql-connector-python
from google.colab import drive
drive.mount('/content/drive')
import mysql.connector
from mysql.connector import Error
import time


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 33.9/33.9 MB 47.1 MB/s eta 0:00:00
Mounted at /content/drive


In [ ]:
MYSQL_HOST = "gateway01.ap-southeast-1.prod.aws.tidbcloud.com"
MYSQL_USER = "4Gu6Uh2tH3NsLam.root"
MYSQL_PASSWORD = "JF4Toi6vzdZzso0d"
MYSQL_PORT = 4000
MYSQL_DATABASE = "Asteroid_Data_5"

In [ ]:
API_KEY = "GtpPyEy4inCnfT9ygkLjLTGYTeiOg2GQ8zsmkI4I"  # Replace with your NASA API key
START_DATE = "2024-01-01"  # Replace with start date (e.g., 2025-06-01)
END_DATE = "2024-01-07"   # Replace with end date (e.g., 2025-06-07)



# FETCHING THE REQUIRED **DATA**

In [ ]:
def fetch_neo_data(START_DATE, END_DATE, API_KEY):
  total_elements = 0
  all_neo_data = []
  url = f"https://api.nasa.gov/neo/rest/v1/feed?start_date={START_DATE}&end_date={END_DATE}&api_key={API_KEY}"
  try:
    while total_elements < 10000:
      response = requests.get(url)
      response.raise_for_status()
      data = response.json()
      total_elements += data["element_count"] #incrementing the element count using next link
      print(f'fetched {data["element_count"]} elements. total so for:{total_elements}')

      for date, neos in data['near_earth_objects'].items():
        all_neo_data.extend(neos)

      if total_elements >= 10000:
        print(f"reached target of 10k datas (Total: {total_elements}).stopping")
        break

      if 'next' in data['links']:
        next_url = data['links']['next']
        url = next_url
      else:
        print("No more links to fetch. stopping.")
        break

    with open('/content/drive/MyDrive/Colab/neo_data_complete.json', 'w') as file:
      json.dump(all_neo_data, file, indent=4)
    print('Data saved to neo_data_complete.json')
    return all_neo_data
  except requests.exceptions.RequestException as e:
    print(f"Error fetching data: {e}")
    return None


fetched 111 elements. total so for:111
fetched 131 elements. total so for:242
fetched 128 elements. total so for:370
fetched 121 elements. total so for:491
fetched 135 elements. total so for:626
fetched 153 elements. total so for:779
fetched 115 elements. total so for:894
fetched 147 elements. total so for:1041
fetched 123 elements. total so for:1164
fetched 111 elements. total so for:1275
fetched 137 elements. total so for:1412
fetched 115 elements. total so for:1527
fetched 116 elements. total so for:1643
fetched 129 elements. total so for:1772
fetched 111 elements. total so for:1883
fetched 140 elements. total so for:2023
fetched 142 elements. total so for:2165
fetched 164 elements. total so for:2329
fetched 126 elements. total so for:2455
fetched 140 elements. total so for:2595
fetched 127 elements. total so for:2722
fetched 134 elements. total so for:2856
fetched 110 elements. total so for:2966
fetched 99 elements. total so for:3065
fetched 102 elements. total so for:3167
fetched 

# CREATING SQL **TABLES**

In [ ]:
def connect_to_mysql():
  try:
    connection = mysql.connector.connect(
        host = MYSQL_HOST,
        user = MYSQL_USERNAME,
        password = MYSQL_PASSWORD,
        port = MYSQL_PORT
    )
    if connection.is_connected():
      cursor = connection.cursor()
      cursor.execute("SHOW DATABASES")
      databases = [db[0] for db in cursor.fetchall()]
      if MYSQL_DATABASE not in databases:
        cursor.execute(f"CREATE DATABASE {MYSQL_DATABASE}")
        print(f"Database '{MYSQL_DATABASE}' created successfully.")
      else:
        print(f"Database '{MYSQL_DATABASE}' already exists.")
      cursor.execute(f"USE {MYSQL_DATABASE}")
      cursor.execute("SHOW TABLES ")
      tables = [table[0] for table in cursor.fetchall()]
      if 'asteroids' not in tables:
        sql_asteroids_creation="""
        CREATE TABLE asteroids (
          asteroid_id INT AUTO_INCREMENT PRIMARY KEY,
          id INT NOT NULL,
          name VARCHAR(255),
          absolute_magnitude_h DECIMAL(10, 2),
          estimated_diameter_min_km DECIMAL(10, 2),
          estimated_diameter_max_km FLOAT,
          is_potentially_hazardous_asteroid BOOLEAN
        );
        """
        cursor.execute(sql_asteroids_creation)
        print("Table 'asteroids' created successfully.")
      else:
        print("Table 'asteroids' already exists.")
      if 'close_approach' not in tables:
        sql_close_approach_creation="""
        CREATE TABLE close_approach (
          approach_id INT AUTO_INCREMENT PRIMARY KEY,
          neo_reference_id INT NOT NULL,
          close_approach_date DATE,
          relative_velocity_kmph FLOAT,
          miss_distance_astronomical FLOAT,
          miss_distance_km FLOAT,
          miss_distance_lunar FLOAT,
          orbiting_body VARCHAR(255)
        );
        """
        cursor.execute(sql_close_approach_creation)
        print("Table 'close_approach' created successfully.")
      else:
        print("Table 'close_approach' already exists.")
      connection.commit()
      return connection, cursor
    else:
      print("failed to connect to mysql:{e}")
  except Error as e:
    print(f"Error connecting to MySQL: {e}")
    return None, None

# INSERTING THE DATA IN SQL

In [ ]:
def insert_neo_data(connection, cursor, asteroids_data, close_approach_data):
  try:
    sql_asteroids_insert = """
    INSERT IGNORE INTO asteroids (id, name, absolute_magnitude_h, estimated_diameter_min_km, estimated_diameter_max_km,
      is_potentially_hazardous_asteroid)
    VALUES (%s, %s, %s, %s, %s, %s)
    """
    asteroids_insert_data = [(
      record['id'],
      record['name'],
      record['absolute_magnitude_h'],
      record['estimated_diameter_min_km'],
      record['estimated_diameter_max_km'],
      record['is_potentially_hazardous_asteroid']
    ) for record in asteroids_data]


    cursor.executemany(sql_asteroids_insert, asteroids_insert_data)
    asteroids_inserted = cursor.rowcount
    print(f"Inserted {asteroids_inserted} new records inserted into 'asteroids' table.(duplicates ignored)")
    sql_close_approach_insert = """
    INSERT IGNORE INTO close_approach (neo_reference_id, close_approach_date, relative_velocity_kmph, miss_distance_astronomical,
      miss_distance_km, miss_distance_lunar, orbiting_body)
    VALUES (%s, %s, %s, %s, %s, %s, %s)
    """

    close_approach_insert_data = [(
        record['neo_reference_id'],
        record['close_approach_date'],
        record['relative_velocity_kmph'],
        record['miss_distance_astronomical'],
        record['miss_distance_km'],
        record['miss_distance_lunar'],
        record['orbiting_body']
    ) for record in close_approach_data]

    cursor.executemany(sql_close_approach_insert, close_approach_insert_data)
    close_approach_inserted = cursor.rowcount
    connection.commit()
    print(f"Inserted {close_approach_inserted} new records inserted into 'close_approach' table.(duplicates ignored)")
  except Error as e:
    print(f"Error inserting data into MySQL: {e}")


# DATA PROCESSING

In [ ]:
def process_neo_data(json_file_path):
  asteroids_data = []
  close_approach_data = []
  try:
    with open(json_file_path, 'r') as file:
      neo_data = json.load(file)
      for index, neo in enumerate(neo_data, start=1):
        try:
          close_approach = neo.get('close_approach_data', [{}])[0]
          asteroid_record = {
              'id':int(neo.get('id')),
              'name':neo.get('name'),
              'absolute_magnitude_h':float(neo.get('absolute_magnitude_h',0.0)),
              'estimated_diameter_min_km':float(neo.get('estimated_diameter',{})
                                                   .get('kilometers',{})
                                                   .get('estimated_diameter_min',{})),
              'estimated_diameter_max_km':float(neo.get('estimated_diameter',{})
                                                   .get('kilometers',{})
                                                   .get('estimated_diameter_max',{})),
              'is_potentially_hazardous_asteroid':neo.get('is_potentially_hazardous_asteroid',False)
          }

          close_approach_record = {
              'neo_reference_id':int(neo.get('id',0)),
              'close_approach_date': None,
              'relative_velocity_kmph': float(close_approach.get('relative_velocity',{}).get('kilometer_per_hour', '0.0')),
              'miss_distance_astronomical': float(close_approach.get('miss_distance',{}).get('astronomical', '0.0')),
              'miss_distance_km': float(close_approach.get('miss_distance',{}).get('kilometers', '0.0')),
              'miss_distance_lunar': float(close_approach.get('miss_distance',{}).get('lunar', '0.0')),
              'orbiting_body': close_approach.get('orbiting_body', 'Unknown')
          }
          date_str = close_approach.get('close_approach_date')
          if date_str:
            try:
              close_approach_record['close_approach_date'] = datetime.strptime(date_str, '%Y-%m-%d').date()
            except ValueError:
              print(f"Invalid date format for{asteroid_record['name']}, setting date to none")
              close_approach_record['close_approach_date'] = None
          if asteroid_record['id'] == 0 or close_approach_record['neo_reference_id'] == 0:
            print(f"warning: skipping record withid or neo_reference_id for {asteroid_record ['name']}")
            continue
          asteroids_data.append(asteroid_record)
          close_approach_data.append(close_approach_record)

        except (ValueError, TypeError) as e:
          print(f"Error processing record for NEO {neo.get('name','unknown')}: {e}")
          continue
    print(f"Processed {len(asteroids_data)} valid asteroid records and {len(close_approach_data)} valid close approach records.")
    with open('asteroids_data.json', 'w') as file:
      json.dump(asteroids_data, file, indent=4, default=str)
    with open('close_approach_data.json', 'w') as file:
      json.dump(close_approach_data, file, indent=4, default=str)
    return asteroids_data, close_approach_data
  except FileNotFoundError:
    print(f"File not found: {json_file_path}")
    return None, None
  except json.JSONDecodeError as e:
    print(f"Error decoding JSON file: {e}")
    return None, None


# MAIN **FUNCTION**

In [ ]:
# Main function
# fetct data from api
neo_data = fetch_neo_data(START_DATE, END_DATE, API_KEY)
# process neo data
json_file_path = '/content/drive/MyDrive/Colab/neo_data_complete.json'

asteroids_data, close_approach_data = process_neo_data(json_file_path)

# print(asteroids_data)
# print(close_approach_data)

# connection to sql
if asteroids_data and close_approach_data:
  connection, cursor = connect_to_mysql()
#insert data to sql
  if connection and cursor:
    insert_neo_data(connection, cursor, asteroids_data, close_approach_data)
    cursor.close()
    connection.close()
    print("MySQL connection closed.")
  print("\nsample of processed asteroid data (first 2 records):")
  for record in asteroids_data[:2]:
    print(record)
  print("\nsample of processed close approach data (first 2 records):")
  for record in close_approach_data[:2]:
    print(record)


Processed 10100 valid asteroid records and 10100 valid close approach records.
[{'id': 2415949, 'name': '415949 (2001 XY10)', 'absolute_magnitude_h': 19.37, 'estimated_diameter_min_km': 0.3552670883, 'estimated_diameter_max_km': 0.7944013596, 'is_potentially_hazardous_asteroid': False}, {'id': 3160747, 'name': '(2003 SR84)', 'absolute_magnitude_h': 26.0, 'estimated_diameter_min_km': 0.0167708462, 'estimated_diameter_max_km': 0.0375007522, 'is_potentially_hazardous_asteroid': False}, {'id': 3309828, 'name': '(2005 YQ96)', 'absolute_magnitude_h': 20.62, 'estimated_diameter_min_km': 0.1997813652, 'estimated_diameter_max_km': 0.4467247133, 'is_potentially_hazardous_asteroid': True}, {'id': 3457842, 'name': '(2009 HC21)', 'absolute_magnitude_h': 22.1, 'estimated_diameter_min_km': 0.1010543415, 'estimated_diameter_max_km': 0.2259643771, 'is_potentially_hazardous_asteroid': False}, {'id': 3553062, 'name': '(2010 XA11)', 'absolute_magnitude_h': 26.1, 'estimated_diameter_min_km': 0.0160160338, 

# SQL **QURIES**

In [ ]:
def connect_to_mysql():
    try:
        connection = mysql.connector.connect(
            host=MYSQL_HOST,
            user=MYSQL_USER,
            password=MYSQL_PASSWORD,
            port=MYSQL_PORT,
            database=MYSQL_DATABASE
        )
        if connection.is_connected():
            return connection
        else:
            st.error("Failed to connect to MySQL server")
            return None
    except Error as e:
        st.error(f"Error connecting to MySQL: {e}")
        return None

# Function to execute a query and return results as a DataFrame
def execute_query(connection, query, params=None):
    try:
        cursor = connection.cursor(dictionary=True)
        if params:
            cursor.execute(query, params)
        else:
            cursor.execute(query)
        results = cursor.fetchall()
        cursor.close()
        return pd.DataFrame(results)
    except Error as e:
        st.error(f"Error executing query: {e}")
        return pd.DataFrame()

# Predefined SQL queries
QUERIES = {
    "Count asteroid approaches":
        SELECT a.name, COUNT(c.approach_id) as approach_count
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        GROUP BY a.id, a.name
        ORDER BY approach_count DESC;
    ,
    "Average velocity per asteroid":
        SELECT a.name, AVG(c.relative_velocity_kmph) as avg_velocity_kmph
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        GROUP BY a.id, a.name
        ORDER BY avg_velocity_kmph DESC;
    ,
    "Top 10 fastest asteroids":
        SELECT a.name, MAX(c.relative_velocity_kmph) as max_velocity_kmph
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        GROUP BY a.id, a.name
        ORDER BY max_velocity_kmph DESC
        LIMIT 10;
    ,
    "Hazardous asteroids with >3 approaches":
        SELECT a.name, COUNT(c.approach_id) as approach_count
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE a.is_potentially_hazardous_asteroid = TRUE
        GROUP BY a.id, a.name
        HAVING approach_count > 3
        ORDER BY approach_count DESC;
    ,
    "Month with most approaches":
        SELECT DATE_FORMAT(c.close_approach_date, '%Y-%m') as month,
               COUNT(*) as approach_count
        FROM close_approach c
        GROUP BY month
        ORDER BY approach_count DESC
        LIMIT 1;
    ,
    "Asteroid with fastest approach":
        SELECT a.name, c.relative_velocity_kmph, c.close_approach_date
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        ORDER BY c.relative_velocity_kmph DESC
        LIMIT 1;
    ,
    "Asteroids by max diameter (descending)":
        SELECT a.name, a.estimated_diameter_max_km
        FROM asteroids a
        ORDER BY a.estimated_diameter_max_km DESC;
    ,
    "Asteroid with decreasing miss distance":
        SELECT a.name, c.close_approach_date, c.miss_distance_astronomical
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE c.miss_distance_astronomical IS NOT NULL
        ORDER BY a.id, c.close_approach_date, c.miss_distance_astronomical;
    ,
    "Closest approach per asteroid":
        SELECT a.name, c.close_approach_date, c.miss_distance_astronomical
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE (a.id, c.miss_distance_astronomical) IN (
            SELECT a2.id, MIN(c2.miss_distance_astronomical)
            FROM asteroids a2
            JOIN close_approach c2 ON a2.id = c2.neo_reference_id
            GROUP BY a2.id
        )
        ORDER BY c.miss_distance_astronomical;
    ,
    "Asteroids with velocity > 50,000 km/h":
        SELECT a.name, c.relative_velocity_kmph, c.close_approach_date
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE c.relative_velocity_kmph > 50000
        ORDER BY c.relative_velocity_kmph DESC;
    ,
    "Approaches per month":
        SELECT DATE_FORMAT(c.close_approach_date, '%Y-%m') as month,
               COUNT(*) as approach_count
        FROM close_approach c
        GROUP BY month
        ORDER BY month;
    ,
    "Asteroid with highest brightness":
        SELECT a.name, a.absolute_magnitude_h
        FROM asteroids a
        WHERE a.absolute_magnitude_h = (
            SELECT MIN(absolute_magnitude_h)
            FROM asteroids
            WHERE absolute_magnitude_h IS NOT NULL
        );
    ,
    "Hazardous vs non-hazardous count":
        SELECT is_potentially_hazardous_asteroid,
               COUNT(*) as asteroid_count
        FROM asteroids
        GROUP BY is_potentially_hazardous_asteroid;
    ,
    "Asteroids closer than Moon (<1 LD)":
        SELECT a.name, c.close_approach_date, c.miss_distance_lunar
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE c.miss_distance_lunar < 1
        ORDER BY c.miss_distance_lunar;
    ,
    "Asteroids within 0.05 AU":
        SELECT a.name, c.close_approach_date, c.miss_distance_astronomical
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE c.miss_distance_astronomical < 0.05
        ORDER BY c.miss_distance_astronomical;
    ,
    "Asteroids with multiple approaches in a year":
        SELECT a.name, DATE_FORMAT(c.close_approach_date, '%Y') as year,
               COUNT(*) as approach_count
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        GROUP BY a.id, a.name, year
        HAVING approach_count > 1
        ORDER BY year, approach_count DESC;
    ,
    "Closest approach by hazardous asteroids":
        SELECT a.name, MIN(c.miss_distance_astronomical) as min_miss_distance_au
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE a.is_potentially_hazardous_asteroid = TRUE
        GROUP BY a.id, a.name
        ORDER BY min_miss_distance_au;
    ,
    "High velocity, small asteroids":
        SELECT a.name, c.relative_velocity_kmph, a.estimated_diameter_max_km
        FROM SSAsteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE c.relative_velocity_kmph > 70000 AND a.estimated_diameter_max_km < 0.1
        ORDER BY c.relative_velocity_kmph DESC;
    ,
    "Average miss distance by orbiting body":
        SELECT c.orbiting_body, AVG(c.miss_distance_lunar) as avg_miss_distance_lunar
        FROM close_approach c
        GROUP BY c.orbiting_body
        ORDER BY avg_miss_distance_lunar;
    ,
    "Largest asteroids with close approaches (<0.1 AU)":
        SELECT a.name, a.estimated_diameter_max_km, MIN(c.miss_distance_astronomical) as min_miss_distance_au
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE c.miss_distance_astronomical < 0.1
        GROUP BY a.id, a.name, a.estimated_diameter_max_km
        ORDER BY a.estimated_diameter_max_km DESC
        LIMIT 10;
    ,
    "Asteroids approaching on specific dates":
        SELECT a.name, c.close_approach_date, c.miss_distance_astronomical
        FROM asteroids a
        JOIN close_approach c ON a.id = c.neo_reference_id
        WHERE c.close_approach_date IN ('2024-01-01', '2024-06-01', '2024-12-31')
        ORDER BY c.close_approach_date;
    ,
    "Brightness vs hazard correlation":
        SELECT
            CASE
                WHEN a.absolute_magnitude_h < 15 THEN '<15 (Very Bright)'
                WHEN a.absolute_magnitude_h < 20 THEN '15-20 (Bright)'
                WHEN a.absolute_magnitude_h < 25 THEN '20-25 (Moderate)'
                ELSE '>=25 (Faint)'
            END as brightness_bin,
            a.is_potentially_hazardous_asteroid,
            COUNT(*) as asteroid_count
        FROM asteroids a
        GROUP BY brightness_bin, a.is_potentially_hazardous_asteroid
        ORDER BY brightness_bin;

}

SyntaxError: invalid syntax. Perhaps you forgot a comma? (ipython-input-19-145424518.py, line 37)